In [1]:
from dotenv import load_dotenv
import os

load_dotenv()
os.environ["OPENAI_API_KEY"] = os.getenv('OPENAI_KEY')

In [2]:
from openai import OpenAI
client = OpenAI()

completion = client.chat.completions.create(
  model="gpt-4o",
  messages=[
    {"role": "system", "content": "You are a helpful assistant."},
    {"role": "user", "content": "Hello!"}
  ]
)

print(completion.choices[0].message)


ChatCompletionMessage(content='Hi there! How can I assist you today?', refusal=None, role='assistant', function_call=None, tool_calls=None)


In [4]:
import getpass
import os
from dotenv import load_dotenv
load_dotenv()

os.environ["MISTRAL_API_KEY"] = os.getenv('MISTRAL_API_KEY1')

In [1]:
from langchain_mistralai import ChatMistralAI

llm = ChatMistralAI(
    model="mistral-large-latest"
)

In [3]:
messages = [
    (
        "system",
        "Trả lời bằng tiếng việt",
    ),
    ("human", "I love programming."),
]
ai_msg = llm.invoke(messages)
ai_msg

LocalProtocolError: Illegal header value b'Bearer '

In [24]:
import os
import random
import time
import json
from typing import List
from qdrant_client import QdrantClient, models
from langchain_core.documents import Document
from langchain_community.embeddings.huggingface import HuggingFaceEmbeddings
from blueprints.rag_utils import format_docs
from blueprints.prompts import QUERY_PROMPT, evaluator_intent, basic_template, chitchat_prompt, safe_prompt, cache_prompt
from langchain.retrievers import EnsembleRetriever
from BM25 import BM25SRetriever
from langchain_mistralai import ChatMistralAI
# from database_Routing import DB_Router
from langchain.retrievers.multi_query import MultiQueryRetriever
from langchain.retrievers.document_compressors import LLMChainExtractor
from langchain_core.output_parsers import StrOutputParser
from langchain_core.output_parsers import BaseOutputParser
# from langchain_cohere import CohereRerank
from langchain.retrievers.contextual_compression import ContextualCompressionRetriever
# from langchain_groq import ChatGroq
import time 
from qdrant_client import QdrantClient
from langchain_community.vectorstores import Qdrant
from langchain.retrievers.document_compressors import LLMChainFilter
from langchain.retrievers.document_compressors import EmbeddingsFilter
from langchain.retrievers.document_compressors import LLMListwiseRerank
from langchain_openai import OpenAIEmbeddings
from dotenv import load_dotenv
from langchain_groq import ChatGroq
load_dotenv()
HF_EMBEDDING =  OpenAIEmbeddings(model='text-embedding-3-small')

class LineListOutputParser(BaseOutputParser[List[str]]):
    """Output parser for a list of lines."""

    def parse(self, text: str) -> List[str]:
        lines = text.strip().split("\n")
        return list(filter(None, lines))  # Remove empty lines

# def extract_metadata(docs, headers=('Header_1', 'Header_2', 'Header_3')):
#     meta_data_docs = []
#     for doc in docs:
#         meta_data_doc = [doc.metadata[header] for header in headers if doc.metadata.get(header)]
#         meta_data_docs.append(meta_data_doc)
#     return meta_data_docs

# def search_with_filter(query, vector_store, k, headers):
#     conditions = [
#         models.FieldCondition(
#             key="metadata.Header_1",
#             match=models.MatchValue(
#                 value=headers[0]
#             ),
#         ),
#         models.FieldCondition(
#             key="metadata.Header_2",
#             match=models.MatchValue(
#                 value=headers[1]
#             ),
#         ),
#     ]


#     if len(headers) == 3:
#         conditions.append(
#             models.FieldCondition(
#                 key="metadata.Header_3",
#                 match=models.MatchValue(
#                     value=headers[2]
#                 ),
#             )
#         )


#     single_result = vector_store.similarity_search(
#         query=query,
#         k=k,
#         filter=models.Filter(
#             must=conditions
#         ),
#     )
    
#     return single_result


if __name__ == "__main__": 

    client = QdrantClient(url="http://localhost:6333")

    stsv = Qdrant(client, collection_name="zaloQA_2022", embeddings= HF_EMBEDDING)
    retriever = stsv.as_retriever(search_kwargs={'k': 3})

    import pickle

    with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/zaloai_2022.pkl', 'rb') as f:
        sotaysinhvien = pickle.load(f)

    retriever_bm25 = BM25SRetriever.from_documents(sotaysinhvien, k= 5, activate_numba = True)

    # reranker = CohereRerank(model = "rerank-multilingual-v3.0", top_n = 5)
#     llm = ChatMistralAI(
#     model="open-mixtral-8x7b",
#     temperature=0,
#     max_retries=2,
# )
    llm1 = ChatGroq(model_name="llama3-70b-8192", temperature=0.1,api_key= os.getenv('llm_api_9'))
    # llm2 = ChatGroq(model_name="llama3-70b-8192", temperature=0.1,api_key= os.getenv('llm_api_5'))
    output_parser = LineListOutputParser()
    llm_chain = QUERY_PROMPT | llm1 | output_parser

    messages = [
        {"role": "system", "content": "Dựa vào thông tin sau, trả lời câu hỏi bằng tiếng việt"}
    ]
import json
import time

def duy_phen():
    with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/500_QA_ZALO.json', 'r', encoding='utf-8') as f:
        corpus = json.load(f)
    sub_corpus = corpus[198:]
    num=1
    for data in sub_corpus:
        user_message = data['question']
        context = data['context']
        if num !=8: 
            num +=1 
        else: num = 1 
    
        api_key_variable = f'llm_api_{num}'
        print(api_key_variable)
        llm = ChatGroq(model_name="llama3-70b-8192", temperature=0.1,api_key= os.getenv(api_key_variable))
        
        start_time = time.time()

        if retriever is not None:
            retriever_multi = MultiQueryRetriever(
                            retriever=retriever, llm_chain=llm_chain, parser_key="lines"
                        ) 

            ensemble_retriever = EnsembleRetriever(
                    retrievers=[retriever_bm25, retriever_multi], weights=[0.5, 0.5])
            
            # compressor = LLMChainExtractor.from_llm(llm)  # Chỉ trích xuất ra thông tin có liên quan để trả về 
            _filter = LLMChainFilter.from_llm(llm)  # Top các tài liệu + lọc ra cái nào cần 
            #_filter2 = LLMListwiseRerank.from_llm(llm, top_n=5)  # như LLMChainFilter nhưng đắt tiền hơn 
            #embeddings_filter = EmbeddingsFilter(embeddings=HF_EMBEDDING, similarity_threshold=0.5) # Truy vấn đươc rồi, so sánh nhúng của doc với question
            compression = ContextualCompressionRetriever(
                        base_compressor=_filter, base_retriever=ensemble_retriever
                        )

            result = compression.invoke(f"{user_message}")
            result = result[:5]
            context_retrieval = []
            for doc in result:  
                 context_retrieval.append(doc.page_content)
            end_time = time.time()
            time.sleep(2)

            output_data = {
                'question': user_message,
                'context-retrieval': context_retrieval,
                'ground-truth': context,
                'latency': end_time-start_time
            }

            # Đọc nội dung của file JSON hiện có
            try:
                with open('qa_zalo_500_compression_LLMChainFilter.json', 'r', encoding='utf-8') as f:
                    existing_data = json.load(f)
            except FileNotFoundError:
                existing_data = []  # Nếu file chưa tồn tại, tạo một danh sách trống

            # Thêm kết quả mới vào danh sách
            existing_data.append(output_data)

            # Ghi lại danh sách đã cập nhật vào file JSON
            with open('qa_zalo_500_compression_LLMChainFilter.json', 'w', encoding='utf-8') as f:
                json.dump(existing_data, f, ensure_ascii=False, indent=4)

        else:
            print('Retriever is not defined. Check output results and ensure retriever is assigned correctly.')

duy_phen()

   

BM25S Create Vocab:   0%|          | 0/500 [00:00<?, ?it/s]

BM25S Convert tokens to indices:   0%|          | 0/500 [00:00<?, ?it/s]

BM25S Count Tokens:   0%|          | 0/500 [00:00<?, ?it/s]

BM25S Compute Scores:   0%|          | 0/500 [00:00<?, ?it/s]

llm_api_2


...

llm_api_6


BM25S Retrieve:   0%|          | 0/1 [00:00<?, ?it/s]

llm_api_7


BM25S Retrieve:   0%|          | 0/1 [00:00<?, ?it/s]

KeyboardInterrupt: 

### mmr 

In [35]:
import json

def calculate_mrr(json_data, k=5):
    total_questions = len(json_data)
    total_mrr = 0

    for entry in json_data:
        context_retrieval = entry.get('context-retrieval', [])
        ground_truth = entry.get('ground-truth', '')

        if not context_retrieval:  # Empty context-retrieval case
            rank = 0
        else:
            try:
                # Try to find the rank of ground-truth within the top k contexts
                rank = context_retrieval[:k].index(ground_truth) + 1
            except ValueError:
                rank = 0  # ground-truth not found in the top k

        if rank > 0:
            total_mrr += 1 / rank

    # Return MRR (if no valid ranks, avoid division by 0)
    return total_mrr / total_questions if total_questions > 0 else 0

# Load your JSON file and calculate MRR
with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/qa_zalo_500_compression_EmbeddingsFilter.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

mrr_value = calculate_mrr(data, k=5)
print(f'MRR@5: {mrr_value}')


MRR@5: 0.538


In [29]:
import json

# Đọc file JSON
def calculate_average_latency(json_file):
    with open(json_file, 'r', encoding='utf-8') as file:
        data = json.load(file)
    
    # Lấy danh sách độ trễ (latency)
    latencies = [item['latency'] for item in data]
    
    # Tính trung bình
    average_latency = sum(latencies) / len(latencies)
    
    return average_latency

# Đường dẫn tới file JSON
json_file = '/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/qa_zalo_500_compression_LLMListwiseRerank.json'

# Gọi hàm tính toán
avg_latency = calculate_average_latency(json_file)
print(f"Độ trễ trung bình: {avg_latency}")


Độ trễ trung bình: 9.304376279830933


In [43]:
from datasets import Dataset 
from ragas.metrics import context_recall
from ragas import evaluate

data_samples = {
    'question': ['Hari Won là người nước nào'],
    'answer': [' '],
    'contexts' : [['Cuộc hôn nhân này không được gia đình nhà vợ đồng thuận , vì khi ấy ba của Hari không có tài sản riêng và tư tưởng của người dân xứ Hàn cũng chưa thật sự cởi mở với hôn thú đa quốc tịch . Vì vậy , cả hai vẫn lấy nhau dù không nhận được bất cứ trợ giúp nào từ gia đình .']],
    'ground_truth': ['Cuộc hôn nhân này không được gia đình nhà vợ đồng thuận , vì khi ấy ba của Hari không có tài sản riêng và tư tưởng của người dân xứ Hàn cũng chưa thật sự cởi mở với hôn thú đa quốc tịch . Vì vậy , cả hai vẫn lấy nhau dù không nhận được bất cứ trợ giúp nào từ gia đình .']
}
dataset = Dataset.from_dict(data_samples)
score = evaluate(dataset,metrics=[context_recall])
score.to_pandas()

Evaluating:   0%|          | 0/1 [00:00<?, ?it/s]

question  \
0  Hari Won là người nước nào   

                                            contexts answer  \
0  [Cuộc hôn nhân này không được gia đình nhà vợ ...          

                                        ground_truth  context_recall  
0  Cuộc hôn nhân này không được gia đình nhà vợ đ...             1.0

### nDCG

In [1]:
import json
import math

# Function to calculate DCG
def dcg(relevances, k):
    """
    Calculate the Discounted Cumulative Gain (DCG) at rank position k.
    
    Parameters:
    - relevances: List of relevance scores (binary or ordinal).
    - k: The rank position up to which DCG is calculated.
    
    Returns:
    - DCG value at rank position k.
    """
    return sum((2**rel - 1) / math.log2(i + 2) for i, rel in enumerate(relevances[:k]))

# Function to calculate nDCG
def ndcg(retrievals, ground_truth, k=5):
    """
    Calculate the normalized Discounted Cumulative Gain (nDCG) at rank position k.
    
    Parameters:
    - retrievals: List of retrieved contexts.
    - ground_truth: The ground truth context for relevance comparison.
    - k: The rank position up to which nDCG is calculated (default is 5).
    
    Returns:
    - nDCG value at rank position k.
    """
    # Handle cases where retrievals might be empty
    if not retrievals:
        return 0.0

    # Assign relevance score of 1 if the context matches ground-truth, else 0
    relevances = [1 if context == ground_truth else 0 for context in retrievals]
    
    # Calculate DCG for the actual retrieval list
    actual_dcg = dcg(relevances, k)
    
    # Calculate IDCG (ideal DCG), where the most relevant items are ranked at the top
    ideal_relevances = sorted(relevances, reverse=True)
    ideal_dcg = dcg(ideal_relevances, k)
    
    # nDCG is actual DCG divided by ideal DCG, with a small adjustment to avoid division by zero
    return actual_dcg / ideal_dcg if ideal_dcg > 0 else 0

# Read JSON data from file
with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/qa_zalo_500_compression_EmbeddingsFilter.json', 'r', encoding='utf-8') as file:
    data = json.load(file)

# Ensure that the data is a dictionary
if isinstance(data, dict):
    # Extract retrievals and ground_truth from the JSON data
    retrievals = data.get('context-retrieval', [])
    ground_truth = data.get('ground-truth', '')

    # Calculate nDCG for this example
    ndcg_score = ndcg(retrievals, ground_truth, k=5)
    print(f"nDCG Score: {ndcg_score:.4f}")
else:
    print("Error: JSON data is not a dictionary.")


Error: JSON data is not a dictionary.


In [8]:
import json
with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/500_QA_ZALO.json', 'r', encoding='utf-8') as f:
    corpus = json.load(f)
sub_corpus = corpus[54:]
for i in sub_corpus: 
    print(i)

{'question': 'Sau khi qua đời, vua Khải Định được an táng tại lăng nào', 'context': 'Lăng Khải Định còn gọi là Ứng Lăng toạ lạc trên triền núi Châu Chữ (còn gọi là Châu Ê) bên ngoài kinh thành Huế là lăng mộ của vua Khải Định, vị vua thứ 12 của triều Nguyễn. Lăng được xây dựng từ năm 1920 ngay sau khi Khải Định lên ngôi. Về kiến trúc lăng Khải Định được người đời sau thường đặt ra ngoài dòng kiến trúc truyền thống thời Nguyễn bởi sự pha trộn kiến trúc Đông Tây Kim Cổ lạ thường, với các tác phẩm nghệ thuật ghép tranh sành sứ độc đáo.'}
{'question': 'Hồ Ba Bể nằm ở tỉnh thành phố nào', 'context': 'Ba Bể là một hồ nước ngọt ở Bắc Kạn, Việt Nam. Nó là một trong một trăm hồ nước ngọt lớn nhất thế giới và nằm trong Vườn quốc gia Ba Bể, nơi đây được công nhận là khu du lịch quốc gia Việt Nam.'}
{'question': 'Nhà máy thủy điện Trị An được xây dựng trên sông nào', 'context': 'Nhà máy Thủy điện Hoà Bình được xây dựng tại hồ Hòa Bình, tỉnh Hòa Bình, trên dòng sông Đà thuộc miền bắc Việt Nam. Đây 

### MAP@k=5

In [39]:
def calculate_map(json_data, k=5):
    total_questions = len(json_data)
    total_map = 0

    for entry in json_data:
        context_retrieval = entry.get('context-retrieval', [])
        ground_truth = entry.get('ground-truth', '')
        
        # Initialize relevant count and sum of precisions
        num_relevant = 0
        sum_precisions = 0
        
        # Iterate over the top k retrieved contexts
        for i, context in enumerate(context_retrieval[:k], start=1):
            if context == ground_truth:
                num_relevant += 1
                # Precision at i: num_relevant / i
                sum_precisions += num_relevant / i
        
        # Calculate AP (if no relevant documents, AP is 0)
        ap = sum_precisions / num_relevant if num_relevant > 0 else 0
        total_map += ap

    # Return MAP (if no questions, avoid division by 0)
    return total_map / total_questions if total_questions > 0 else 0

# Load your JSON file and calculate MAP
with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/qa_zalo_500_compression_LLMChainFilter.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

map_value = calculate_map(data, k=5)
print(f'MAP@5: {map_value}')


MAP@5: 0.6833333333333333


### ndcg

In [6]:
import json
import numpy as np

def calculate_dcg(relevance_scores):
    dcg = 0
    for i, score in enumerate(relevance_scores):
        dcg += score / np.log2(i + 2)
    return dcg

def calculate_ndcg(context_retrieval, ground_truth):
    # Determine relevance scores
    relevance_scores = [1 if ground_truth in context else 0 for context in context_retrieval]
    
    # Calculate DCG for given relevance scores
    dcg = calculate_dcg(relevance_scores)
    
    # Calculate IDCG for the ideal case (relevance scores sorted in descending order)
    ideal_relevance_scores = sorted(relevance_scores, reverse=True)
    idcg = calculate_dcg(ideal_relevance_scores)
    
    # Calculate nDCG
    ndcg = dcg / idcg if idcg > 0 else 0
    
    return ndcg

def process_json_file(input_file, output_file):
    with open(input_file, 'r', encoding='utf-8') as f:
        data = json.load(f)
    
    results = []
    total_ndcg = 0
    count = 0
    
    for item in data:
        question = item.get('question')
        context_retrieval = item.get('context-retrieval', [])
        ground_truth = item.get('ground-truth', '')
        latency = item.get('latency')
        
        ndcg_score = calculate_ndcg(context_retrieval, ground_truth)
        
        results.append({
            'question': question,
            'nDCG Score': ndcg_score,
            'latency': latency
        })
        
        total_ndcg += ndcg_score
        count += 1
    
    # Calculate average nDCG
    average_ndcg = total_ndcg / count if count > 0 else 0
    print(average_ndcg)
    # Add average nDCG to results
    results.append({
        'average_nDCG Score': average_ndcg
    })
    
    # Save results to output file
    with open(output_file, 'w', encoding='utf-8') as f:
        json.dump(results, f, ensure_ascii=False, indent=4)

# Replace 'input.json' and 'output.json' with your file names
process_json_file('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/qa_zalo_500_compression_LLMListwiseRerank.json', 'output.json')


0.8023982906305129


### hit@5

In [9]:
import json

def calculate_hit_at_5(data):
    """
    Tính toán Hit@5 cho một danh sách các đối tượng JSON.
    
    :param data: Danh sách các đối tượng JSON chứa các trường 'question', 'context-retrieval', 'ground-truth'.
    :return: Tỷ lệ phần trăm của các câu hỏi mà mục đúng nằm trong top 5 của danh sách truy hồi ngữ cảnh.
    """
    hit_count = 0
    total_count = len(data)
    
    for item in data:
        context_retrieval = item.get('context-retrieval', [])
        ground_truth = item.get('ground-truth', '')
        
        # Chỉ lấy top 5 context-retrieval
        top_contexts = context_retrieval[:5]
        
        if ground_truth in top_contexts:
            hit_count += 1
    
    hit_at_5 = (hit_count / total_count) * 100 if total_count > 0 else 0
    return hit_at_5

def main():
    # Đọc dữ liệu từ file JSON
    file_path = '/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/qa_zalo_500_compression_LLMListwiseRerank.json'  # Thay đổi đường dẫn đến file JSON của bạn
    
    with open(file_path, 'r', encoding='utf-8') as file:
        data = json.load(file)
    
    # Tính toán Hit@5
    hit_at_5 = calculate_hit_at_5(data)
    print(f"Hit@5: {hit_at_5}%")

if __name__ == "__main__":
    main()


Hit@5: 86.8%


In [37]:
import json

def compare_fields(json_data):
    total_entries = len(json_data)
    total_score = 0
    
    for entry in json_data:
        ground_truth = entry.get("ground-truth", "").strip()
        context_retrieval = entry.get("context-retrieval", "").strip()
        
        # Remove single quotes at the start and end of context_retrieval
        context_retrieval = context_retrieval.strip("'")
        
        # Compare the fields
        if ground_truth == context_retrieval:
            total_score += 1
            
    # Calculate the average score
    average_score = total_score / total_entries if total_entries > 0 else 0
    return average_score

# Load the JSON data from a file
with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/qa_zalo_500_bm25.json', 'r', encoding='utf-8') as file:
    json_data = json.load(file)

# Get the average score
average = compare_fields(json_data)
print(f"The average score is: {average}")


The average score is: 0.754


### sử dụng vector db 

In [6]:
import os
import time
import json
from typing import List
from qdrant_client import QdrantClient, models
from langchain_core.documents import Document
from langchain_community.embeddings.huggingface import HuggingFaceEmbeddings
from blueprints.rag_utils import format_docs
from blueprints.prompts import QUERY_PROMPT, evaluator_intent, basic_template, chitchat_prompt, safe_prompt, cache_prompt
from langchain.retrievers import EnsembleRetriever
from BM25 import BM25SRetriever
from langchain_mistralai import ChatMistralAI
# from database_Routing import DB_Router
from langchain.retrievers.multi_query import MultiQueryRetriever
from langchain.retrievers.document_compressors import LLMChainExtractor
from langchain_core.output_parsers import StrOutputParser
from langchain_core.output_parsers import BaseOutputParser
# from langchain_cohere import CohereRerank
from langchain.retrievers.contextual_compression import ContextualCompressionRetriever
# from langchain_groq import ChatGroq
import time 
from qdrant_client import QdrantClient
from langchain_community.vectorstores import Qdrant
from langchain.retrievers.document_compressors import LLMChainFilter
from langchain.retrievers.document_compressors import EmbeddingsFilter
from langchain.retrievers.document_compressors import LLMListwiseRerank
from langchain_openai import OpenAIEmbeddings
from dotenv import load_dotenv
from langchain_groq import ChatGroq
load_dotenv()
HF_EMBEDDING =  OpenAIEmbeddings(model='text-embedding-3-small')

class LineListOutputParser(BaseOutputParser[List[str]]):
    """Output parser for a list of lines."""

    def parse(self, text: str) -> List[str]:
        lines = text.strip().split("\n")
        return list(filter(None, lines))  # Remove empty lines

# def extract_metadata(docs, headers=('Header_1', 'Header_2', 'Header_3')):
#     meta_data_docs = []
#     for doc in docs:
#         meta_data_doc = [doc.metadata[header] for header in headers if doc.metadata.get(header)]
#         meta_data_docs.append(meta_data_doc)
#     return meta_data_docs

# def search_with_filter(query, vector_store, k, headers):
#     conditions = [
#         models.FieldCondition(
#             key="metadata.Header_1",
#             match=models.MatchValue(
#                 value=headers[0]
#             ),
#         ),
#         models.FieldCondition(
#             key="metadata.Header_2",
#             match=models.MatchValue(
#                 value=headers[1]
#             ),
#         ),
#     ]


#     if len(headers) == 3:
#         conditions.append(
#             models.FieldCondition(
#                 key="metadata.Header_3",
#                 match=models.MatchValue(
#                     value=headers[2]
#                 ),
#             )
#         )


#     single_result = vector_store.similarity_search(
#         query=query,
#         k=k,
#         filter=models.Filter(
#             must=conditions
#         ),
#     )
    
#     return single_result


if __name__ == "__main__": 

    client = QdrantClient(url="http://localhost:6333")

    stsv = Qdrant(client, collection_name="zaloQA_2022", embeddings= HF_EMBEDDING)
    retriever = stsv.as_retriever(search_kwargs={'k': 3})
    # result = retriever.invoke("Hari Won là người nước nào")

    import pickle

    with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/zaloai_2022.pkl', 'rb') as f:
        sotaysinhvien = pickle.load(f)

    retriever_bm25 = BM25SRetriever.from_documents(sotaysinhvien, k= 5, activate_numba = True)

    # reranker = CohereRerank(model = "rerank-multilingual-v3.0", top_n = 5)
    llm = ChatMistralAI(
    model="open-mixtral-8x7b",
    temperature=0,
    max_retries=2,
)
    llm1 = ChatGroq(model_name="llama3-70b-8192", temperature=0.1,api_key= os.getenv('llm_api_4'))
    # llm2 = ChatGroq(model_name="llama3-70b-8192", temperature=0.1,api_key= os.getenv('llm_api_5'))
    output_parser = LineListOutputParser()
    llm_chain = QUERY_PROMPT | llm1 | output_parser

    messages = [
        {"role": "system", "content": "Dựa vào thông tin sau, trả lời câu hỏi bằng tiếng việt"}
    ]
import json
import time

def duy_phen():
        # user_message = input("Nhập câu hỏi của bạn: ")
        user_message = "Dãy núi nào được coi là biểu tượng của tỉnh Quảng Bình"
        if retriever is not None:
            # retriever_multi = MultiQueryRetriever(
            #                 retriever=retriever, llm_chain=llm_chain, parser_key="lines"
            #             ) 

            # ensemble_retriever = EnsembleRetriever(
            #         retrievers=[retriever_bm25, retriever_multi], weights=[0.5, 0.5])
            
            # compressor = LLMChainExtractor.from_llm(llm)
            # _filter = LLMChainFilter.from_llm(llm)
            # _filter2 = LLMListwiseRerank.from_llm(llm, top_n=1)
            # embeddings_filter = EmbeddingsFilter(embeddings=HF_EMBEDDING, similarity_threshold=0.5)
            # compression = ContextualCompressionRetriever(
            #             base_compressor=_filter2, base_retriever=ensemble_retriever
            #             )

            result = retriever_bm25.invoke(f"{user_message}")
            print(result)
            end_time = time.time()


        else:
            print('Retriever is not defined. Check output results and ensure retriever is assigned correctly.')

duy_phen()

   

AttributeError: 'list' object has no attribute 'page_content'

In [ ]:
gthv_db = gthv.as_retriever(search_kwargs={'k': 3})
gthv_db.invoke('Giám đốc học viện hiện tại là ai? ')

### Trải nghiệm bộ zaloQA 2022

In [16]:
import random
def load_questions_from_json(file_path):
    """
    Đọc file JSON và thêm câu hỏi vào vector_store.
    
    :param file_path: Đường dẫn đến file JSON.
    :param vector_store: Đối tượng vector store của bạn.
    """

    with open(file_path, 'r', encoding='utf-8') as json_file:
        data = json.load(json_file)
    corpus =  random.sample(data['data'], 1000)
    for sample in corpus:
        print(sample['text'])
load_questions_from_json("/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/zac2022_train_merged_final.json")

Đến năm 1955 chức vụ Thủ tướng được chuyển giao cho Phó Thủ tướng lúc đó là Phạm Văn Đồng đảm nhiệm . Hồ Chí Minh là Chủ tịch đầu tiên của nước Việt Nam Dân chủ Cộng hoà , được Quốc hội khoá II bầu lại và làm Chủ tịch đến khi ông mất ngày 2 tháng 9 năm 1969 .
Các năm thường có các tháng với số ngày là 29 và 30, xếp xen kẽ nhau với ngày nhuận sẽ được thêm vào tháng Jyestha (Nayon) làm cho nó có 30 ngày. Tháng nhuận thu được bằng cách tính tháng Ashadha (Waso) hai lần. Mỗi tháng có nửa trăng tròn dần dài 15 ngày và nửa trăng khuyết dần dài 14 hoặc 15 ngày.
Giá nhà trung bình tại Canberra trong tháng 9 năm 2009 là 511.820 AUD, chỉ thấp hơn Sydney song số các thành phố thủ đô và thủ phủ có trên 100.000 dân, vượt qua Melbourne và Perth từ năm 2005. Chi phí thuê nhà của cư dân Canberra cao hơn so với giá thuê tại tất cả các bang và lãnh thổ khác.
Bột thì là Ai Cập cũng có thể dùng để nêm nhiều món ăn, do nó làm giảm độ ngọt tự nhiên của các món ăn này. Thông thường nó hay được thêm vào các m

In [15]:
import json 
import random
with open("/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/zac2022_train_merged_final.json", 'r', encoding='utf-8') as file: 
    data = json.load(file)
# data['data']
sample_list = random.sample(data['data'], 1000)
for i in sample_list: 
    print(i['text'])

Chāhan Nhật Bản được coi là một món ăn Nhật Bản gốc Hoa , có nguồn gốc từ các món cơm chiên Trung Quốc .
1. Huyện Đại An không có núi. Riêng 7 xã ở huyện Vụ Bản có 9 ngọn núi, đều dùng tên núi để đặt tên làng. Một ngọn ở xã Trang Nghiêm, 3 ngọn ở xã Tiên Hương, 1 ngọn ở xã Lê Xá, 2 ngọn ở 2 xã Đăng Côi và Mỹ Côi, 1 ngọn ở xã Xuân Bảng, 1 ngọn ở xã Hổ Sơn.
Lan Hà tên đầy đủ là Đỗ Nguyễn Lan Hà, là một diễn viên người Việt Nam. Lan Hà đến với điện ảnh khi cô mới 13 tuổi, cô được thủ vai Gianh trong bộ phim "Đời Cát" của đạo diễn  Nguyễn Thanh Vân . Với vai diễn này cô đã giành được giải "Nữ diễn viên phụ xuất sắc" tại Liên hoan phim Việt Nam lần 13. Một vai diễn khác của Lan Hà cũng đã gặt hái được nhiều thành công, đó chính là vai Mai trong bộ phim "Trái tim bé bỏng". Với vai Mai, Lan Hà đã được trao giải thưởng "Nữ diễn viên chính xuất sắc nhất" tại lễ trao giải Cánh diều vàng năm 2007 và nhận được giải Bông sen vàng tại Liên hoan phim Việt Nam năm 2009.  Chỉ với hai vai diễn Lan Hà đã

In [4]:
from langchain_qdrant import QdrantVectorStore
from qdrant_client import QdrantClient
from qdrant_client.http.models import Distance, VectorParams
from langchain_openai import OpenAIEmbeddings
from dotenv import load_dotenv
import os
from langchain_community.embeddings.huggingface import HuggingFaceEmbeddings
HF_EMBEDDING = HuggingFaceEmbeddings(model_name="dangvantuan/vietnamese-embedding")
load_dotenv()

embeddings = OpenAIEmbeddings(model='text-embedding-3-small')


client = QdrantClient("localhost:6333")

client.create_collection(
    collection_name="zaloQA_2022",
    vectors_config=VectorParams(size=1536, distance=Distance.COSINE),
)
# 1536

vector_store = QdrantVectorStore(
    client=client,
    collection_name="zaloQA_2022",
    embedding=embeddings,
)

You try to use a model that was created with version 2.6.1, however, your version is 2.5.1. This might cause unexpected behavior or errors. In that case, try to update to the latest version.





In [5]:
import json
import pickle
from uuid import uuid4
from langchain_core.documents import Document

# List to store all documents
all_documents = []

# Hàm thêm tài liệu vào vector_store
def add_document_to_vector_store(vector_store, page_content):
    """
    Thêm một tài liệu mới vào vector_store.
    
    :param vector_store: Đối tượng vector store của bạn.
    :param page_content: Nội dung chính của tài liệu (câu hỏi).
    """
    # Tạo document mới
    new_document = Document(page_content=page_content)
    
    # Tạo UUID cho document
    new_id = str(uuid4())
    
    # Thêm document vào vector_store
    vector_store.add_documents(documents=[new_document], ids=[new_id])
    
    # Lưu document vào list
    all_documents.append(new_document)
    
    print(f"Document with ID {new_id} added to vector store.")

# Đọc file JSON và load câu hỏi
import random
def load_questions_from_json(file_path, vector_store):
    """, 
    Đọc file JSON và thêm câu hỏi vào vector_store.
    
    :param file_path: Đường dẫn đến file JSON.
    :param vector_store: Đối tượng vector store của bạn.
    """

    with open(file_path, 'r', encoding='utf-8') as json_file:
        data = json.load(json_file)
    corpus =  random.sample(data['data'], 500)
    for sample in corpus:
            add_document_to_vector_store(
                vector_store=vector_store,
                page_content=sample['text'] 
            )

# Lưu documents vào file .pkl
def save_documents_to_pkl(documents, file_name):
    """
    Lưu danh sách tài liệu vào file .pkl.
    
    :param documents: Danh sách các tài liệu cần lưu.
    :param file_name: Tên file .pkl.
    """
    with open(file_name, 'wb') as f:
        pickle.dump(documents, f)
    print(f"Documents saved to {file_name}")

# Ví dụ gọi hàm
file_path = '/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/zac2022_train_merged_final.json'
load_questions_from_json(file_path, vector_store)

# Lưu documents vào file pkl sau khi đã thêm hết
pkl_file_path = 'zaloai_2022.pkl'
save_documents_to_pkl(all_documents, pkl_file_path)


Document with ID 0d202591-af7b-4252-957b-0ff2757c901f added to vector store.
Document with ID 0464ce93-54c2-4a84-ad02-c7605976c696 added to vector store.
Document with ID 85fed649-cb5a-4baf-8051-439429d2578d added to vector store.
Document with ID 2a9f258f-068b-47c2-b535-b54d284293c8 added to vector store.
Document with ID fa7cd723-0e0c-4aa4-a415-c748dcff0d34 added to vector store.
Document with ID 3b251781-2a5d-45b3-8607-4361284a932f added to vector store.
Document with ID dd025387-a803-4a26-a8fd-c2d8fb6a42ca added to vector store.
Document with ID 0a3305ef-9396-46a8-8085-86e69242a311 added to vector store.
Document with ID 36f21c6c-fce9-46bc-8a8d-e5a100e9f498 added to vector store.
Document with ID 73f4afcb-d1be-4c94-9f15-a34104fc9571 added to vector store.
Document with ID 98086884-430e-487a-b1df-409829cfa80e added to vector store.
Document with ID c41331b9-4618-4d2a-803c-7030fe5a7da6 added to vector store.
Document with ID 912104a3-c06e-46f0-8edf-773f58215b9b added to vector store.

In [27]:
text_list = []
for docs in all_documents: 
    text_list.append(docs.page_content)
print(len(text_list))

500


In [22]:
import json

# Bước 2: Đọc nội dung file JSON chứa các trường text, question, và context
with open('/home/justtuananh/AI4TUAN/DOAN2024/offical/pipelines/zac2022_train_merged_final.json', 'r', encoding='utf-8') as f:
    json_data = json.load(f)

# Bước 3: Tạo một danh sách để chứa các kết quả matching
output_data = []
num = 0 
# Bước 4: So sánh text từ danh sách với text trong file JSON
for item in json_data['data']:
    json_text = item['text']
    json_question = item['question']
    
    if json_text in text_list:
        num += 1 
        # Nếu text trùng khớp, lưu question và context vào file khác
        output_data.append({
            'question': json_question,
            'context': json_text
        })

# Bước 5: Ghi các kết quả matching vào file JSON khác
with open('sub_zaloQA_2022.json', 'w', encoding='utf-8') as f:
    json.dump(output_data, f, ensure_ascii=False, indent=4)

print("Đã ghi kết quả vào file output.json")
print(num)


Đã ghi kết quả vào file output.json
678
